In [1]:
import os
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import animation
from IPython.display import HTML

In [2]:
EDGES = [
    (0, 1), (1, 2), (2, 3), (3, 4),        # spine + neck/head
    (3, 5), (5, 6), (6, 7),                # arm
    (3, 8), (8, 9), (9, 10),               # arm
    (0, 11), (11, 12), (12, 13), (13, 14), (14, 15),  # leg (includes toe)
    (0, 16), (16, 17), (17, 18), (18, 19), (19, 20),  # leg (includes toe)
]

step = 'sample_step015000'

motion = np.load(f'./kit-ml-diffusion/{step}.npy')

text = open(f'./kit-ml-diffusion/{step}.txt', 'r').read().strip()


T, J, _ = motion.shape
print("Frames:", T, "Joints:", J)

Frames: 76 Joints: 21


In [3]:
def animate_skeleton(motion, edges, caption, stride=1, elev=15, azim=-70, interval=33, lim_pad=0.2):
    motion = motion[::stride].copy()
    T, J, _ = motion.shape

    motion -= motion[:, [0], :]

    mins = motion.reshape(-1, 3).min(axis=0)
    maxs = motion.reshape(-1, 3).max(axis=0)
    span = (maxs - mins).max()
    center = (maxs + mins) / 2
    half = span / 2 * (1 + lim_pad)

    fig = plt.figure(figsize=(6, 6))
    ax = fig.add_subplot(111, projection="3d")
    ax.view_init(elev=elev, azim=azim)

    ax.set_xlim(center[0] - half, center[0] + half)
    ax.set_ylim(center[1] - half, center[1] + half)
    ax.set_zlim(center[2] - half, center[2] + half)

    ax.set_xlabel("X")
    ax.set_ylabel("Y")
    ax.set_zlabel("Z")

    pts = ax.scatter([], [], [], s=20)
    lines = []
    for _ in edges:
        ln, = ax.plot([], [], [], linewidth=2)
        lines.append(ln)

    def init():
        pts._offsets3d = ([], [], [])
        for ln in lines:
            ln.set_data([], [])
            ln.set_3d_properties([])
        return [pts] + lines

    def update(t):
        frame = motion[t]
        xs, ys, zs = frame[:, 0], frame[:, 2], frame[:, 1]
        pts._offsets3d = (xs, ys, zs)

        for k, (i, j) in enumerate(edges):
            lines[k].set_data([xs[i], xs[j]], [ys[i], ys[j]])
            lines[k].set_3d_properties([zs[i], zs[j]])

        ax.set_title(f"{caption} | frame {t+1}/{T}")
        return [pts] + lines

    ani = animation.FuncAnimation(fig, update, frames=T, init_func=init, interval=interval, blit=True)
    plt.close(fig)
    return ani

ani = animate_skeleton(motion, EDGES, step)
display(HTML(ani.to_jshtml()))
print(text)

A person laying on their hands and knees stands up by using their left foot first, then pushing off it to stay balanced.
